In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import pickle as pkl
import numpy as np
import random
import torch
import torchvision
import avalanche as ava

/home/boehlke/programs/anaconda3/envs/ava-test5/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Introduction to Avalance
This Notebook provides some example code which should act as a start off point to understand the inner workings of the avalnche framework and extentsions made. The way in which thecode in this notebook is written should make it easy to follow where the different Classes are impoted from and thereby understand the code and its application. 

### Checking if GPU is recognized: 

In [3]:
use_cuda = torch.cuda.is_available()
detected_device = torch.device("cuda:0" if use_cuda else "cpu")
detected_device

device(type='cuda', index=0)

### Importing Data:

In [5]:
images_root = '/home/AMMOD_data/camera_traps/BayerWald/G-Fallen/MDcrops/'
data_dir_path = os.path.join(os.getcwd(), '../../data/')
train_stream_file = data_dir_path+'data_stream_files/BW_stream_files/cv0_expsize128_crop_train_stream.pkl'
test_stream_file = data_dir_path+'data_stream_files/BW_stream_files/cv0_expsize128_crop_test_stream.pkl'
label_dict_file = data_dir_path+'label_dictionaries/BIRDS_11_Species.pkl'
with open(train_stream_file, 'rb') as handle: # even for training with stream of exp size384 128 needs to be loaded first to match the winter stream files
    train_stream = pkl.load(handle)
with open(test_stream_file, 'rb') as handle: # even for training with stream of exp size384 128 needs to be loaded first to match the winter stream files
    test_stream = pkl.load(handle)
with open(label_dict_file, 'rb') as handle:
    label_dict = pkl.load(handle)


### Defining Model Parameters and Data Augmentations

In [6]:
resize = int(224/0.875)
data_transforms = {
    'train': torchvision.transforms.Compose([
        torchvision.transforms.Resize((resize,resize)),
        torchvision.transforms.RandomCrop(size=(224,224)),
        torchvision.transforms.RandomHorizontalFlip(), 
        torchvision.transforms.ToTensor(),
        torchvision.transforms.ColorJitter(brightness=0.3, contrast=0.3, saturation=0.3, hue=0.1), 
        torchvision.transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    'val': torchvision.transforms.Compose([
        torchvision.transforms.Resize((224,224)),
        torchvision.transforms.ToTensor(),
        torchvision.transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
    ]),
    }


model = ava.models.pytorchcv_wrapper.resnet('imagenet', depth=18, pretrained=True)
model.num_classes = 11
num_input_ftrs = model.output.in_features
model.output = torch.nn.Linear(num_input_ftrs , model.num_classes)
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.AdamW(model.parameters(), eps=1e-4, weight_decay=75e-3)
batchsize = 128

###  Instantiating Avalanche's Basic Metrics and Logging Classes 
#### (combined in the Evaluation Plugin)

In [ ]:
tb_logger = ava.logging.TensorboardLogger(tb_log_dir="./logging_example/without_seq_id/tb_data", filename_suffix='test_run')
csv_logger = ava.logging.CSVLogger(log_folder='./logging_example/without_seq_id/csvlogs')
interactive_logger = ava.logging.InteractiveLogger()

# This following avalanche function returns a list of accuracy metrics 
# that are evaluated at different invtervals during the training/evaluation loop
metrics = ava.evaluation.accuracy_metrics(stream=True, experience=True)

combined_logger = ava.training.EvaluationPlugin(
    metrics,
    loggers=[tb_logger, csv_logger, interactive_logger],
    suppress_warnings=True)




# Datastream Without Sequence Information

The data loaded from the data_stream_files folder is camerat trap data, where each piece of data comes with the path, label and sequence identifier. In order to simplify things at the start and demonstrate the usage in cases without sequence ids, we are removing the sequence_id from the stream data. 

In [ ]:
train_stream_without_seq = [[(tupel[0], tupel[1]) for tupel in sublist] for sublist in train_stream]
test_stream_without_seq = [(tupel[0], tupel[1]) for tupel in test_stream]

### Defining the Strategy
Next, we are instanciating the Basestrategy class (Naive) or the child of the Basestrategy class (Cumulative) in case we want to cumulatively train the Model. The Basestrategy class defines a training loop with several callback functions at different stages in the training/evaluation cycle that are called by 'Plugins'. At this stage, the plugins list is empty, but the evaluator is basically a plugin, that calls the different callback functions, and checks whether any of the metrics have to be updated at each point in the loop.

In [ ]:
naive_strategy = ava.training.Naive(
    model, optimizer, criterion,  
    train_mb_size=batchsize, train_epochs=1, eval_mb_size=batchsize, device=detected_device, plugins=[], evaluator=combined_logger)

cumulative_strategy = ava.training.Cumulative(
    model, optimizer, criterion, train_mb_size=batchsize, train_epochs=1, eval_mb_size=batchsize, device=detected_device, plugins=[], evaluator=combined_logger)


### Avalanche Scenario
Next, the so-called scenario instance is created, by which avalanche combines the data and augmentations. The paths_benchmark function is actually called create_generic_benchmark_from_paths (defined in benchmarks/scenarios/generic_benchmark_creation.py). It is renamed in benchmarks/generators/benchmark_generators.py for some reason...

Theoriginal Avalanche function was modified to take a path_dataset variable, which should be a child class of the Pytorch Dataset class. In this case we use the PathsDataset class defined in benchmarks/utils/datasets_from_filelists.py 

In [ ]:
# In many continuous learning applications, a model should learn different 'tasks' (groups of classes).
# In our case this is not relavant, so all pieces of data belong to the same task: 0
task_labels = np.zeros((1,len(train_stream))).astype(int).tolist()[0] 

# generic_scenario = ava.benchmarks.scenarios.generic_benchmark_creation.create_generic_benchmark_from_paths(...
# calls the same funciton as:
scenario = ava.benchmarks.paths_benchmark(
   train_stream_without_seq,
   [test_stream_without_seq],  
   task_labels=task_labels,
   complete_test_set_only=True,
   train_transform=data_transforms['train'],
   eval_transform=data_transforms['val'],
   path_dataset_class=ava.benchmarks.PathsDataset,
   common_root = images_root
)


In [ ]:
# Here the train function from the strategy is called for each sublist in the train_stream. 
# Then the eval function is called on the test stream. This function could also be called on the train stream,
# which would evaluate all metrics on the entire train stream and might take a long time, since the train stream
# is three times as large as the test_stream. 

number_workers = 4
cl_strategy = naive_strategy # or cumulative_strategy

for i, experience in enumerate(scenario.train_stream):
    cl_strategy.train(experience, num_workers=number_workers)
    print('Training completed')
    #cl_strategy.eval(scenario.train_stream, num_workers=number_workers)
    print('Computing accuracy on the whole test set')
    cl_strategy.eval(scenario.test_stream, num_workers=number_workers)

### Standard Joint Training As A Baseline
When we want to tain a simple model in the standard way, i.e, all data is available to the model at once, the Naive (Basestrategy) instance is used and the training loop is modified slightly.  Here it is important to instantiate the Naive Basestrategy with train_epochs=1 and define the number of epochs used in the loop seperately. Surely, there is a different way to do this too, but this works with the logging the way I want it to. Also, the train_stream is modified to be a list with a single list of data tuples.

In [ ]:
joint_train_stream_without_seq = [item for sublist in train_stream_without_seq for item in sublist ]
random.shuffle(joint_train_stream_without_seq)

tb_logger = ava.logging.TensorboardLogger(tb_log_dir="./logging_example/joint_training/tb_data", filename_suffix='test_run')
csv_logger = ava.logging.CSVLogger(log_folder='./logging_example/joint_training/csvlogs')
interactive_logger = ava.logging.InteractiveLogger()

# This following avalanche function returns a list of accuracy metrics 
# that are evaluated at different invtervals during the training/evaluation loop
metrics = ava.evaluation.accuracy_metrics(stream=True, experience=True)

combined_logger = ava.training.EvaluationPlugin(
    metrics,
    loggers=[tb_logger, csv_logger, interactive_logger],
    suppress_warnings=True)


scenario = ava.benchmarks.paths_benchmark(
   joint_train_stream_without_seq,
   [test_stream_without_seq],  
   task_labels=task_labels,
   complete_test_set_only=True,
   train_transform=data_transforms['train'],
   eval_transform=data_transforms['val'],
   path_dataset_class=ava.benchmarks.PathsDataset,
   common_root = images_root
)

naive_strategy = ava.training.Naive(
    model, optimizer, criterion,  
    train_mb_size=batchsize, train_epochs=1, eval_mb_size=batchsize, device=detected_device, plugins=[], evaluator=combined_logger)

nr_of_epochs = 9
number_workers = 4
cl_strategy = naive_strategy # or cumulative_strategy

for i in range(nr_of_epochs):
    cl_strategy.train(joint_train_stream_without_seq, num_workers=number_workers)
    print('Training completed')
    #cl_strategy.eval(scenario.train_stream, num_workers=number_workers)
    print('Computing accuracy on the whole test set')
    cl_strategy.eval(scenario.test_stream, num_workers=number_workers)

## Track Sequnece Information in Avalanche
In order to track sequence wise metrics, the information about the sequence affiliations of each image need to be available in the training/testing loop. This was implemented using the SeqPathsDataset class, which is an extension of the Python Dataset class that handles a third field (addditionally to image path and labell), the sequence id. Further, the SeqDataPlugin was added with a modified \_unpack\_minibatch callback function that is called during the training/evaluation loop to handle the third seq_id field that the Dataloader of the SeqPathsDataset returns. This plugin also keeps track  of class occurance statistics and saves the targets and predictions during evaluation.
This data is collected here to produce comprehensive visualisations of results in form of confusion matricies later on.

In [ ]:

tb_logger = ava.logging.TensorboardLogger(tb_log_dir="./logging_example/seq_id_data/tb_data", filename_suffix='test_run')
csv_logger = ava.logging.CSVLogger(log_folder='./logging_example/seq_id_data/csvlogs')
interactive_logger = ava.logging.InteractiveLogger()

# This following avalanche function returns a list of accuracy metrics 
# that are evaluated at different invtervals during the training/evaluation loop
metrics = ava.evaluation.accuracy_metrics(stream=True, experience=True)

combined_logger = ava.training.EvaluationPlugin(
    metrics,
    loggers=[tb_logger, csv_logger, interactive_logger],
    suppress_warnings=True)

seq_plugin = ava.training.plugins.SeqDataPlugin()
naive_strategy = ava.training.Naive(
    model, optimizer, criterion,  
    train_mb_size=32, train_epochs=1, eval_mb_size=48, device=detected_device, plugins=[seq_plugin], evaluator=combined_logger)

cumulative_strategy = ava.training.Cumulative(
    model, optimizer, criterion, train_mb_size=48, train_epochs=1, eval_mb_size=96, device=detected_device, plugins=[seq_plugin], evaluator=combined_logger)


task_labels = np.zeros((1,len(train_stream))).astype(int).tolist()[0] 
scenario = ava.benchmarks.paths_benchmark(
   train_stream,
   [test_stream],  
   task_labels=task_labels,
   complete_test_set_only=True,
   train_transform=data_transforms['train'],
   eval_transform=data_transforms['val'],
   path_dataset_class=ava.benchmarks.SeqPathsDataset,
   common_root = images_root
)



number_workers = 4
cl_strategy = naive_strategy # or cumulative_strategy


In [ ]:
for i, experience in enumerate(scenario.train_stream):
    cl_strategy.train(experience, num_workers=number_workers)
    print('Training completed')
    #cl_strategy.eval(scenario.train_stream, num_workers=number_workers)
    print('Computing accuracy on the whole test set')
    cl_strategy.eval(scenario.test_stream, num_workers=number_workers)

## Comprehensive Metrics and Generic Logger

In order to get a better understanding of the performance of different continual leaning / rehearsal strategies, several different metrics were implemented. This includes sequence-wise metrics, class-wise metrics, season-based evaluations and several more. See the /evaluation/metrics/accuracy.py implementation comments for more details.

Each metric inherits from the GenericPluginMetric class defined in /metrics/metric\_definitions.py which coordinates the update()-/reset()-/result()- function call of the metrics at different stages during the training, depending on whether the metric is calculated over an iteration, experience, epoch or stream. More precisely, the EvaluationPlugin has a funciton called \_update\_metrics() which calls the callback function of the GenericPluginMetric which again calls the appropriate update()-/reset()-/result()- function for each metric and collects the results in a list called metric_values at the appropriate stage. Then the evalutaion plugin also calls all loggers and passes the metric_values list as an argument. 

The GenericPluginMetric was written to handle the newly added accuracy metrics. It is unfortunately not as generic as the name makes it out to be. It could definately be improved upon. Also the implementation of the metrics could be improved to avoid for example the looping over sequence ids or computing the same updates more than once for similar metrics like class-wise accuracies for each class and class avg accuracy. The metrics that are evaluated for every epoch, experience or iteration are quite slow. Doing this after each epoch/experience/iteration would mean that the whole training-evaluation process would take a very long time. 

when calling the eval function of the naive strategy (base\_strategy) i have added the optional boolean variable 'last_eval', which, if true means a confusion matrix and dictionary is pickled that contains all sorts of infomration on the current metrics, predictions, targets and so on. This implemented to allow quick overviews of the performance of sdifferent methods. The data for this confusion matrix is collected at different points in the evaluation/training cycle and saved as variables of the strategy. Currently, it is required that some specific metrics are tracked when last_eval is true so that these variables are set. A work aroud could be easily implemented. Also, a label_dict file has to be passed to the strategy.  The actual confusion plot is created in the after\_eval() callback funciton of the Evaluation Plugin in evaluation\_plugin()



In [7]:
label_dict_path = os.path.join(os.getcwd(), '../../data/label_dictionaries/BIRDS_11_Species.pkl')
with open(label_dict_path, 'rb') as handle:
     label_dict = pkl.load(handle)


In [8]:
file = 'cv0_expsize128_crop'
data_streams_path = os.path.join(os.getcwd(), '../../data/data_stream_files/BW_stream_files/')
with open(data_streams_path+file.replace('384','128')+'_winter_val_stream.pkl', 'rb') as handle:
     validation_stream_winter = pkl.load(handle)

with open(data_streams_path+file.replace('384','128')+'_winter_test_stream.pkl', 'rb') as handle:
    test_stream_winter = pkl.load(handle)

with open(data_streams_path+file.replace('_crop','').replace('384','128')+'_exp_season_split_dict.pkl', 'rb') as handle:
    exp_season_split_dict = pkl.load(handle)
    
validation_stream_winter_files = np.array(validation_stream_winter)[:,0]
validation_stream_winter_files = [images_root+s[0:] for s in validation_stream_winter_files ]
test_stream_winter_files = np.array(test_stream_winter)[:,0]
test_stream_winter_files = [images_root+s[0:] for s in test_stream_winter_files ]

winter_exp = exp_season_split_dict['winter']
summer_exp = exp_season_split_dict['summer']
winter_train_exp = [train_stream[i] for i in winter_exp]
all_winter_train_data = [i for sublist in winter_train_exp for i in sublist]
all_winter_train_files = np.array(all_winter_train_data)[:,0]
all_winter_train_files = [images_root+s[0:] for s in all_winter_train_files ]
all_winter_files = all_winter_train_files +test_stream_winter_files+validation_stream_winter_files


In [9]:
nc =11 #number of classes

metrics = [ava.metrics.accuracy.Top1AccTransfer(nr_train_exp=len(train_stream), reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.ClassTop_nAvgAcc(nr_classes=nc, n=1, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.ClassTop_nAvgAcc(nr_classes=nc, n=2, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonClassTop_nAcc(nr_classes=nc, n=1, winter_files_list=all_winter_files, season='summer', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonClassTop_nAcc(nr_classes=nc, n=1, winter_files_list=all_winter_files, season='winter', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.ClasswiseTop_nAcc(nr_classes=nc, n=1, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.Top_nAcc(n=1, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonTop_nAcc(n=1, winter_files_list=all_winter_files, season='summer', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonTop_nAcc(n=1, winter_files_list=all_winter_files, season='winter', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.Top_nAcc(n=2, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeqTop_nAcc(n=1, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeqMaxAcc( reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonSeqTop_nAcc(num=1, winter_files_list=all_winter_files, season='summer', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonSeqTop_nAcc(num=1, winter_files_list=all_winter_files, season='winter', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeqClasswiseTop_nAcc(nr_classes=nc, n=1, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeqClassTop_nAvgAcc(nr_classes=nc, n=1, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeqClassAvgMaxAcc(nr_classes=nc, reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonSeqClassTop_nAcc(nr_classes=nc, n=1, winter_files_list=all_winter_files, season='summer', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeasonSeqClassTop_nAcc(nr_classes=nc, n=1, winter_files_list=all_winter_files, season='winter', reset_at='stream', emit_at='stream', mode='eval'),
           ava.metrics.accuracy.SeqAnyAcc(reset_at='stream', emit_at='stream', mode='eval')]


In [10]:
tb_logger = ava.logging.TensorboardLogger(tb_log_dir="./logging_example/comprehnesive_metrics/tb_data", filename_suffix='test_run')
csv_logger = ava.logging.GenericCSVLogger(log_folder='./logging_example/comprehnesive_metrics/csvlogs')
interactive_logger = ava.logging.InteractiveLogger()
combined_logger = ava.training.EvaluationPlugin(
    metrics,
    loggers=[tb_logger, csv_logger, interactive_logger],
    suppress_warnings=True)

seq_plugin = ava.training.plugins.SeqDataPlugin()
naive_strategy = ava.training.Naive(
    model, optimizer, criterion,  
    train_mb_size=32, train_epochs=1, 
    eval_mb_size=48, device=detected_device, 
    plugins=[seq_plugin], evaluator=combined_logger,
    label_dict=label_dict)

number_workers = 8
task_labels = np.zeros((1,len(train_stream))).astype(int).tolist()[0] 
scenario = ava.benchmarks.paths_benchmark(
   train_stream,
   [test_stream],  
   task_labels=task_labels,
   complete_test_set_only=True,
   train_transform=data_transforms['train'],
   eval_transform=data_transforms['val'],
   path_dataset_class=ava.benchmarks.SeqPathsDataset,
   common_root = images_root
)

last_eval = True

In [ ]:
cl_strategy = naive_strategy
for i, experience in enumerate(scenario.train_stream):
    cl_strategy.train(experience, num_workers=number_workers)
    print('Training completed')
    #cl_strategy.eval(scenario.train_stream, num_workers=number_workers)
    print('Computing accuracy on the whole test set')
    cl_strategy.eval(scenario.test_stream, num_workers=number_workers, last_eval= last_eval)

-- >> Start of training phase << --
Start of experience:  0
Current Classes:  [10, 3, 4]
-- Starting training on experience 0 (Task 0) from train stream --
0it [00:00, ?it/s]

/home/boehlke/AMMOD/avalanche_extension/avalanche/avalanche/training/plugins/sequence_data.py:104: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  strategy.seq_codes = torch.tensor(strategy.mbatch[2][0]).to(strategy.device)


100%|████████████████████████████████████████████████████████████████████████████████████████████████| 4/4 [00:15<00:00,  3.96s/it]
Epoch 0 ended.
-- >> End of training phase << --
Training completed
Computing accuracy on the whole test set
-- >> Start of eval phase << --
-- Starting eval on experience 0 (Task 0) from test stream --
 34%|██████████████████████████████▊                                                             | 120/358 [01:56<03:41,  1.08it/s]

## Rehearsal Learning 

In the examples so far, the strategy for continual learning meant either a naive approach (finetuning with latest new data) or a cumulative approach (finetuning with all data seen so far). A bunch of methods were implemented to use the rehearsal approach to continual learning to ensure the model does not overwrite previously learned knowledge when finetuning with the new incoming data. The idea is to select images from the memory strategically and use them together with the new data to fine tune the model. 

The main functionalities of this approach where implemented in the ClassImbalanceRehersalPlugin class in /avalanche/training/plugins/imbalance_focus_replay.py. Each instance of this class or child class needs to pass the 'buffer\_data\_ratio' variable which defines how many images from the memory are selcted for each images in the current experience. The callback function train_dataset_adaptation() is called to create a AvalancheSubset of the memory data by using the indicies for the memory data returned by the \_get\_indices() function, which is implemented by the child class. If the memory is not yet large enough, the entire memory is used for rehearsal. After the finetuning is completed, the after\_training\_exp() callback function is called to add the current experience to the memory. 

A full list of all the child classes implementing different rehearsal selection methods:
MaximallyInterferedRetrievalRehersalPlugin, 
RandomRehersal, 
ClassErrorRehersalPlugin, 
ClassErrorRehersalTemperaturePlugin, 
ClassFrequencyRehearsalPlugin, 
WeightedeMovingClassErrorAverageRehersalPlugin,
ClassErrorFrequencyAvgRehearsalPlugin,
FillExpBasedRehearsalPlugin,
FillExpOversampleBasedRehearsalPlugin

A more detailed description of what they do and how they are implemented can be found in the comments under each class definition in imbalance_focus_replay.py

To use these rehearsal strategies, the correct plugin just has to be added to the list of plugins for the Naive strategy class.  
In the following the use of the class error based rehearsal method is demonstrated. In order to use this rehearsal strategy, validation data is necessary to estimate the clas error rates. Further it is required to use the ClasswiseTop_nAcc with n=1 as a metric, where the validation data's class accuracies are stored in a stratedy variable. The validation data needs to be used for evaluation at least once, before the plugin aims to select images from the memory. 



In [ ]:
val_stream_file = data_dir_path+'data_stream_files/BW_stream_files/cv0_expsize128_crop_val_stream.pkl'
label_dict_file = data_dir_path+'label_dictionaries/BIRDS_11_Species.pkl'
with open(val_stream_file, 'rb') as handle: 
    val_stream = pkl.load(handle)
# The val_stream is passed to the pahts_benchmark function below, that creats the 'scenario'

In [ ]:
tb_logger = ava.logging.TensorboardLogger(tb_log_dir="./logging_example/rehearsal_learning/tb_data", filename_suffix='test_run')
csv_logger = ava.logging.GenericCSVLogger(log_folder='./logging_example/rehearsal_learning/csvlogs')
interactive_logger = ava.logging.InteractiveLogger()
combined_logger = ava.training.EvaluationPlugin(
    metrics,
    loggers=[tb_logger, csv_logger, interactive_logger],
    suppress_warnings=True)

number_workers = 8
task_labels = np.zeros((1,len(train_stream))).astype(int).tolist()[0] 
scenario = ava.benchmarks.paths_benchmark(
   train_stream,
   [test_stream],  
   other_streams_lists_of_files={'validation': [val_stream]},
   task_labels=task_labels,
   complete_test_set_only=True,
   train_transform=data_transforms['train'],
   eval_transform=data_transforms['val'],
   path_dataset_class=ava.benchmarks.SeqPathsDataset,
   common_root = images_root
)


seq_plugin = ava.training.plugins.SeqDataPlugin()
class_error_method = ava.training.plugins.ClassErrorRehersalPlugin(buffer_data_ratio=1)
plugins_list = [seq_plugin, class_error_method]

naive_strategy = ava.training.Naive(
    model, optimizer, criterion,  
    train_mb_size=32, train_epochs=1, eval_mb_size=48, device=detected_device, plugins=plugins_list, evaluator=combined_logger)


In [ ]:
cl_strategy = naive_strategy
for i, experience in enumerate(scenario.train_stream):
    cl_strategy.train(experience, num_workers=number_workers)
    print('Training completed')
    cl_strategy.eval(scenario.validation_stream, num_workers=number_workers, last_eval=True)
    print('Computing accuracy on the whole test set')
    cl_strategy.eval(scenario.test_stream, num_workers=number_workers, last_eval=True)

## Rehearsal Learning with Limited Memory 

In the real world, there will never be a unlimited memory. Two memory filling strategies were implemented in /avalanche/training/plugins/class_balancing_replay.py. These are the baseline stadnard reservoir sampling used to draw uniformly from a stream and a strategy specifically designed for class imbalace called class balancing reservoir sampling ('Online Continual Learning from Imbalanced Data' by Chrysakis et al.)


In [ ]:
tb_logger = ava.logging.TensorboardLogger(tb_log_dir="./logging_example/rehearsal_learning_limited_memory/tb_data", filename_suffix='test_run')
csv_logger = ava.logging.GenericCSVLogger(log_folder='./logging_example/rehearsal_learning_limited_memory/csvlogs')
interactive_logger = ava.logging.InteractiveLogger()
combined_logger = ava.training.EvaluationPlugin(
    metrics,
    loggers=[tb_logger, csv_logger, interactive_logger],
    suppress_warnings=True)

number_workers = 8
task_labels = np.zeros((1,len(train_stream))).astype(int).tolist()[0] 
scenario = ava.benchmarks.paths_benchmark(
   train_stream,
   [test_stream],  
   other_streams_lists_of_files={'validation': [val_stream]},
   task_labels=task_labels,
   complete_test_set_only=True,
   train_transform=data_transforms['train'],
   eval_transform=data_transforms['val'],
   path_dataset_class=ava.benchmarks.SeqPathsDataset,
   common_root = images_root
)


seq_plugin = ava.training.plugins.SeqDataPlugin()
plugin_cbrs = ava.training.plugins.ClassBalancingReservoirMemoryRehersalPlugin(buffer_data_ratio=1, memory_size=500, nr_classes=11, 
                                                          rehearsal_selection_strategy='ce', temperature=0.2)
plugins_list = [seq_plugin, plugin_cbrs]

naive_strategy = ava.training.Naive(
    model, optimizer, criterion,  
    train_mb_size=32, train_epochs=1, eval_mb_size=48, device=detected_device, plugins=plugins_list, evaluator=combined_logger)







In [ ]:
cl_strategy = naive_strategy
for i, experience in enumerate(scenario.train_stream):
    cl_strategy.train(experience, num_workers=number_workers)
    print('Training completed')
    cl_strategy.eval(scenario.validation_stream, num_workers=number_workers)
    print('Computing accuracy on the whole test set')
    cl_strategy.eval(scenario.test_stream, num_workers=number_workers)